#  Captioning Demo

### Imports

In [40]:
import io
import base64
import glob
import os

import gzip
import json
import numpy as np
import torch
from IPython.display import HTML
from skvideo.io import FFmpegReader, ffprobe, vwrite
from torch.autograd import Variable

### Tool to deal with mpeg videos

In [41]:
def show_video(video_filenames):
    """
    Tool to display videos inside the notebook.
    """
    
    if type(video_filenames) is not list:
        video_filenames = [video_filenames]
    
    html_code = ''
    for filename in video_filenames:
        video = io.open(filename, 'r+b').read()
        encoded = base64.b64encode(video)
        html_code += '''
        <video alt="test" width="640" height="480" controls>
        <source src="data:video/mp4;base64,{0}" type="video/mp4" />
        </video>
        '''.format(encoded.decode('ascii'))
        
    return HTML(data= html_code)


def open_mpeg_video(fname, framerate, size):
    """
    Open an mpeg video, and return it as a numpy array.
    """
    
    metadata = ffprobe(fname)
    duration = float(metadata['video']['@duration'])
    # Compute corresponding nb of frames
    nframes = int(duration * framerate)
    oargs = {
        "-r": "%d" % framerate,
        "-vframes": "%d" % nframes,
        "-s": "%dx%d" % (size[0], size[1])
    }
    # Open file
    reader = FFmpegReader(fname, inputdict={}, outputdict=oargs)
    video = []
    # Get frames until there is no more
    for frame in reader.nextFrame():
        video.append(frame)
    # Return as a numpy array
    return np.array(video)

## A) Model Instantiation

In [42]:
from ptcap.model.captioners import EncoderDecoder
from ptcap.model.encoders import CNN3dLSTMEncoder
from ptcap.model.pretrained_encoders import FCEncoder, JesterEncoder, BIJesterEncoder
from ptcap.model.decoders import LSTMDecoder

#net = FullyConvolutionalNet(num_classes=178)jester1024_cutoff_300_ssssssss/

net = EncoderDecoder(
        encoder=BIJesterEncoder,
        decoder=LSTMDecoder,
        encoder_kwargs={"freeze": False},#, "pretrained_path": "/home/farzaneh/PycharmProjects/pretrained_nets/fully_conv_net_on_smtsmt_20170627/model.checkpoint"},
        decoder_kwargs={"embedding_size": 256, "go_token": 0, "gpus": [0], "hidden_size": 1024, "num_lstm_layers": 1, 
        "vocab_size": 2986}, 
        gpus=[0]).cuda()

gpus: [0]
****************************************************************************************************
()
{'freeze': False}
()
{'go_token': 0, 'vocab_size': 2986, 'embedding_size': 256, 'gpus': [0], 'num_lstm_layers': 1, 'hidden_size': 1024}
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&


### Total number of parameters

In [43]:
num_params = sum([np.prod(param.size()) 
                  for param in net.parameters()])
print('Total number of parameters: {}'.format(num_params))

Total number of parameters: 17118268


## B) Loading weights

Send me a message if you want these weights

In [44]:
path = '/home/farzaneh/PycharmProjects/pytorch-captioning/results/jester1024_cutoff_5_unfrozen_lbl_lr=0.0001/'
checkpoint = torch.load(path + '/model.best')
net.load_state_dict(checkpoint["model"])

## C) Load Tokenizer

In [52]:
from ptcap.data.tokenizer import Tokenizer

USER_MAXLEN=17
tokenizer = Tokenizer(user_maxlen=USER_MAXLEN)
tokenizer.load_dictionaries(path)

## C) Testing 

In [53]:
TMP_VIDEO_FILENAME = 'tmp.mp4'

def unpreprocess(video):
    video = video.data.numpy()[0]
    video = 64. * video.transpose(1, 2, 3, 0)
    return np.array(video, 'uint8')

def demo(net, preprocessor, filename, top_n=5):
    # Open mpeg file and get a numpy array
    video_uint8 = open_mpeg_video(filename, 12, [128, 128])
    # Preprocessing
    video = preprocessor(video_uint8)
    # Convert to torch variable
    video = Variable(torch.from_numpy(video[None]), volatile=True).cuda()
    empty_caption = Variable(torch.zeros([1, USER_MAXLEN]), volatile=True).long().cuda()
    
    # Compute predictions
    pred = net.forward((video, empty_caption), use_teacher_forcing=False)
    # Convert to numpy 
    pred = np.exp(pred.cpu().data.numpy())[0]
    # Class index
    pred_argmax = np.argmax(pred, axis=1)
    decoded_pred = tokenizer.decode_caption(pred_argmax)
    print(decoded_pred)
    # Print class name with proba
    # Save input video in tmp file
    vwrite(TMP_VIDEO_FILENAME, unpreprocess(video.cpu()))
    return show_video([TMP_VIDEO_FILENAME, filename])

def path_generator(annotation_path, root_path):
    with gzip.open(annotation_path, "rt") as f:
        annotations = json.load(f)
    files = [elem['file'] for elem in annotations]
    labels = [elem['label'] for elem in annotations]
    return ((os.path.join(root_path, f), label) for f,label in zip(files, labels))

In [54]:
# Path generator
path_gen = path_generator('/data/20bn-somethingsomething/json/test_20170929.json.gz', 
                          '/data/20bn-somethingsomething/videos')
# Put the network in evaluation mode
_ = net.eval()

#### Preprocessor

In [55]:
from rtorchn.data.preprocessing import default_evaluation_preprocesser

preprocessor = default_evaluation_preprocesser([48, 96, 96], 64.)

#### Ctrl + Enter

In [56]:
path_to_video = '/data/20bn-somethingsomething/videos/1280777/large_784c5d1a26c362a6d62e.mp4'
label = 'pretending to pick pencil up'
print('Label: {}\n{}'.format(label, 65*'-'))
demo(net, preprocessor, path_to_video)

Label: pretending to pick pencil up
-----------------------------------------------------------------
['PRETENDING', 'TO', 'PICK', 'A', 'PEN', 'UP', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>']


In [58]:
path_to_video = '/data/20bn-somethingsomething/videos/68388/large_70e5a95d0cdb621ecae9.mp4'
label = 'pouring water into cup'

print('Label: {}\n{}'.format(label, 65*'-'))
demo(net, preprocessor, path_to_video)

Label: pouring water into cup
-----------------------------------------------------------------
['TRYING', 'TO', 'POUR', 'WATER', 'INTO', 'CUP', 'BUT', 'MISSING', 'SO', 'IT', 'SPILLS', 'NEXT', '<END>', '<END>', '<END>', '<END>', '<END>']


In [59]:
path_to_video = '/data/20bn-somethingsomething/videos/1152240/large_e5f44f4114aeb04e5b31.mp4'
label = 'moving a pencil and a pencil closer to each other'

print('Label: {}\n{}'.format(label, 65*'-'))
demo(net, preprocessor, path_to_video)

Label: moving a pencil and a pencil closer to each other
-----------------------------------------------------------------
['MOVING', 'PEN', 'AND', 'PENCIL', 'CLOSER', 'TO', 'EACH', 'OTHER', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>']


In [60]:
path_to_video = '/data/20bn-somethingsomething/videos/668717/large_eca1e613437ef0ba7aab.mp4'
label = 'taking the phone out of the box'

print('Label: {}\n{}'.format(label, 65*'-'))
demo(net, preprocessor, path_to_video)

Label: taking the phone out of the box
-----------------------------------------------------------------
['UNCOVERING', 'A', 'BOOK', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>']


In [61]:
path_to_video

'/data/20bn-somethingsomething/videos/668717/large_eca1e613437ef0ba7aab.mp4'

In [62]:
path_to_video = '/data/20bn-somethingsomething/videos/36742/large_123fc4c216d498b661ec.mp4'
label = 'piling books up'

print('Label: {}\n{}'.format(label, 65*'-'))
demo(net, preprocessor, path_to_video)

Label: piling books up
-----------------------------------------------------------------
['COVERING', 'A', 'BOOK', 'WITH', 'A', 'PAPER', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>']


In [63]:
path_to_video = '/data/20bn-somethingsomething/videos/43495/large_28270fd5892ec7024093.mp4'
label = 'piling books up'

print('Label: {}\n{}'.format(label, 65*'-'))
demo(net, preprocessor, path_to_video)

Label: piling books up
-----------------------------------------------------------------
['PRETENDING', 'TO', 'BE', 'TEARING', 'A', 'BOOK', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>']


In [217]:
path_to_video, label = next(path_gen)

print('Label: {}\n{}'.format(label, 65*'-'))
demo(net, preprocessor, path_to_video)

Label: wiping board off of duster
-----------------------------------------------------------------
['WIPING', 'DUST', 'OFF', 'OF', 'TABLE', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>', '<END>']


In [165]:
path_to_video = '/data/20bn-somethingsomething/videos/75106/large_4ece053758babe72979b.mp4'